For convert datasets please download last version of dataset [https://nomeroff.net.ua/datasets/](https://nomeroff.net.ua/datasets/). Unpack archive and rename to **./datasets/** .
For examle
```bash
cd ./datasets
wget https://nomeroff.net.ua/datasets/autoriaNumberplateDataset-2019-09-17.zip
unzip autoriaNumberplateDataset-2019-09-17.zip
mv autoriaNumberplateDataset-2019-09-17 numberplates
```
or use your own dataset.

# COCO Convertor

In [1]:
# import libs
import os
import glob
import copy
import numpy as np
from PIL import Image
import json

In [2]:
# init coco blocks
coco = {
    "info": {},
    "licenses": [],
    "images": [],
    "annotations": [],
    "categories": [],
    "segment_info": []
}

In [3]:
# init info block
coco["info"] = {
    "description": "NumberPlate Dataset",
    "url": "https://nomeroff.net.ua",
    "version": "0.3.1",
    "year": 2019,
    "contributor": "RIA.com Marketplaces",
    "date_created": "2019/09/17"
}

In [4]:
# init licenses block
coco["licenses"] = [
    {
        "url": "https://github.com/ria-com/nomeroff-net/blob/master/LICENSE",
        "id": 1,
        "name": "GNU General Public License v3.0"
    }
]

In [5]:
# init categories
coco["categories"] = [
    {"supercategory": "vehicle","id": 1,"name": "numberplate"}
]

In [6]:
# create own coco datasets from VIA VGG
ROOT_DIR = "../../datasets/numberplates"
DATASETS = ["train", "val"]
VIA_JSON_NAMES = ["train/via_region_data.json", "val/via_region_data.json"]

ALLOWED_FORMATS = ["png", "jpg", "jpeg"]

# init default data
coco_datasets = {}
for dataset in DATASETS:
    coco_datasets[dataset] = copy.deepcopy(coco)

In [7]:
# load images
for dataset in DATASETS:
    for _id, img_path in enumerate(glob.glob(f"{os.path.join(ROOT_DIR, dataset)}/*")):
        if os.path.basename(img_path).split(".")[-1].lower() not in ALLOWED_FORMATS:
            continue
        # get image metadata
        image = Image.open(img_path)
        exif = image.getexif()
        creation_time = exif.get(36867)
        width, height = image.size
        
        # append in coco dataset format
        coco_datasets[dataset]["images"].append({
            "license": 1,
            "file_name": os.path.basename(img_path),
            "coco_url": "https://nomeroff.net.ua/datasets/autoriaNumberplateDataset-2019-09-17.zip",
            "height": height,
            "width":  width,
            "date_captured": creation_time,
            "flickr_url": "http://farm7.staticflickr.com/6116/6255196340_da26cf2c9e_z.jpg",
            "id": _id
        })

In [8]:
def PolygonSort(corners):
    n = len(corners)
    cx = float(sum(x for x, y in corners)) / n
    cy = float(sum(y for x, y in corners)) / n
    cornersWithAngles = []
    for x, y in corners:
        an = (np.arctan2(y - cy, x - cx) + 2.0 * np.pi) % (2.0 * np.pi)
        cornersWithAngles.append((x, y, an))
    cornersWithAngles.sort(key = lambda tup: tup[2])
    return  [(x, y) for x, y, an in cornersWithAngles]

def PolygonArea(corners):
    n = len(corners)
    area = 0.0
    for i in range(n):
        j = (i + 1) % n
        area += corners[i][0] * corners[j][1]
        area -= corners[j][0] * corners[i][1]
    area = abs(area) / 2.0
    return area

In [9]:
# add annotations
annotation_id = 0
for json_data_path, dataset in zip(VIA_JSON_NAMES, DATASETS):
    with open(os.path.join(ROOT_DIR, json_data_path)) as jsonFile:
        json_data = json.load(jsonFile)
    for key in json_data["_via_img_metadata"]:
        metadata = json_data["_via_img_metadata"][key]
        
        # define image_id
        image_file_name = metadata["file_name"]
        image_id = [x["id"] for x in coco_datasets[dataset]["images"] if x["file_name"] == image_file_name][0]
            
        for region in metadata["regions"]:
            segmentation = [[]]
            for x, y in zip(region["shape_attributes"]["all_points_x"], region["shape_attributes"]["all_points_y"]):
                segmentation[0].append(x)
                segmentation[0].append(y)
            
            # define area
            corners = [(x, y) for x, y in zip(region["shape_attributes"]["all_points_x"], region["shape_attributes"]["all_points_y"])]
            corners_sorted = PolygonSort(corners)
            area = PolygonArea(corners_sorted)
            
            # define category_id
            category_name = region["region_attributes"]["class"]
            #category_ids = [x["id"] for x in coco_datasets[dataset]["categories"] if x["name"] == category_name]
            
            #if not len(category_ids):
            #    continue
            category_id = 1#category_ids[0]
            # define bbox
            x_min = min([c[0] for c in corners])
            x_max = max([c[0] for c in corners])
            y_min = min([c[1] for c in corners])
            y_max = max([c[1] for c in corners])
            
            
            # appent annotation
            coco_datasets[dataset]["annotations"].append({
                "segmentation": segmentation,
                "area": area,
                "iscrowd": 0,
                "image_id": image_id,
                "bbox": [x_min, y_min, x_max-x_min, y_max-y_min],
                "category_id": category_id,
                "id": annotation_id
            })
            annotation_id += 1
                

In [10]:
# save datasets json
for dataset in DATASETS:
    with open(os.path.join(ROOT_DIR, dataset, "coco_numberplate.json"), "w") as jsonFile:
        json.dump(coco_datasets[dataset], jsonFile)

# Detectron2

In [11]:
# Regist own dataset.
from detectron2.data.datasets import register_coco_instances


# train data
name        = "numberplate_train"
json_file   = os.path.abspath("../../datasets/numberplates/train/coco_numberplate.json")
image_root  = os.path.abspath("../../datasets/numberplates/train")

# test data
name_val        = "numberplate_val"
json_file_val   = os.path.abspath("../../datasets/numberplates/val/coco_numberplate.json")
image_root_val  = os.path.abspath("../../datasets/numberplates/val")

# registr
register_coco_instances(name, {}, json_file, image_root)
register_coco_instances(name_val, {}, json_file_val, image_root_val)

In [12]:
import random
from detectron2.data import DatasetCatalog, MetadataCatalog
from detectron2.utils.visualizer import Visualizer
from matplotlib import pyplot as plt


# get dataset
metadata = MetadataCatalog.get("numberplate_train")
dataset_dicts = DatasetCatalog.get("numberplate_train")

In [13]:
metadata

namespace(name='numberplate_train',
          json_file='/mnt/storage2/var/www/nomeroff-net/datasets/numberplates/train/coco_numberplate.json',
          image_root='/mnt/storage2/var/www/nomeroff-net/datasets/numberplates/train',
          evaluator_type='coco',
          thing_classes=['numberplate'],
          thing_dataset_id_to_contiguous_id={1: 0})

In [14]:
def imshow(img):
    plt.rcParams["figure.figsize"] = (20, 20)
    plt.axis("off")
    plt.imshow(img)
    plt.show()

In [15]:
for d in random.sample(dataset_dicts, 3):
    img = plt.imread(d["file_name"])
    visualizer = Visualizer(img[:, :, ::], metadata=metadata, scale=0.5)
    vis = visualizer.draw_dataset_dict(d)
    imshow(vis.get_image()[:, :, ::])